#Readme

This notebook calculates the load duration curve and heating demands for a simulation of a single building

*Duration:* The duration for which you want to analysis. Can be one of the following: *day/week/month/year*

*result:* Result file name relative to this notebook

In [7]:
duration = 'year'
result = '../../Results/haarhakker-year-occ4.mat'

## Contents

- [Real time powers](#Powers)
- [Load duration curves](#Load-duration-curves)

In [8]:
import sys
sys.path.append('/home/arnout/Projects/Work/python-highcharts')

from modelicares import SimRes, SimResList
from charts import plot, plotasync

import numpy as np
import datetime

In [9]:
if duration == 'day':
    duration = 86400
elif duration == 'week':
    duration = 60400
elif duration == 'month':
    duration = 2400000
else:
    duration = 31556926 - 86400

print duration

31470526


In [10]:
load_names = {
    'hea.Q_flow': 'Total heat flow',
    'buildingTest.heatingSystem.QHeaSys': 'Heating system heat flow'
}

In [27]:
def toseries(sim, key, t=None, neg=False):
    def tonp(v):
        return np.array(map(lambda u: u._value, v))
    
    if not t:
        x = sim[key].times()
    else:
        x = t
    
    y = tonp(sim[key].values(x))
    if not neg:
        y[y<0] = 0
    
    x = map(lambda u: u*1000, x)
    
    return np.array([x,y]).T

In [12]:
data = SimRes(result)

In [20]:
# Equi-distant time vector
minutes = 15
points = duration / (60*minutes)
t = [60*minutes*i for i in range(24*(60/minutes), points)]

dates = map(datetime.datetime.fromtimestamp, t)   

# Get the loads at times t
loads = []
for name, description in load_names.iteritems():
    loads.append(dict(name=description, data=toseries(data, name, t)))
    
# Get the DHW load
y = np.array(loads[0]['data'])[:,1] - np.array(loads[1]['data'])[:,1]
y[y<0] = 0 
x = map(lambda u: u*1000, t)

loads.append(dict(name='DHW heat flow', data=np.array([x,y]).T))

### Powers
Plot of the real time powers of the building

In [22]:
options = {
    'chart': {
        'zoomType': 'xy'
    },
    'legend': {
        'enabled': True
    }
}

plot(loads, options, stock=True, show='inline', height=550)

In [23]:
## Load duration curve calculations

# Sort by power
ldcTotal = sorted(loads[0]['data'], lambda x,y: cmp(y[1], x[1]))
ldcHeating   = sorted(loads[1]['data'], lambda x,y: cmp(y[1], x[1]))
ldcDHW = sorted(loads[2]['data'], lambda x,y: cmp(y[1], x[1]))

# Reset time 
ldcTotal   = [[t[i]*1000, x[1]] for i,x in enumerate(ldcTotal)]
ldcHeating = [[t[i]*1000, x[1]] for i,x in enumerate(ldcHeating)]
ldcDHW     = [[t[i]*1000, x[1]] for i,x in enumerate(ldcDHW)]

# Create series array
series = [
    dict(name='Total', data=ldcTotal),
    dict(name='Heating', data=ldcHeating),
    dict(name='DHW', data=ldcDHW)
]

### Load duration curves

In [26]:
plot(series, options, show='inline', stock=True, height=550)